<h3>Векторизуем словарь Meddra</h3>

Загрузим srobert'у

In [1]:
from sentence_transformers import SentenceTransformer

#роберта с mean pooling
model = SentenceTransformer('all-distilroberta-v1')

In [2]:
class ConceptVectorizer():
    def __init__(self, thesaurus_path):
        self.meddra_codes = []
        self.meddra_code_to_meddra_term = {}
        self.meddra_term_to_meddra_code = {}
        with open(thesaurus_path, "r") as f:
            for meddra_line in f:
                meddra_line = meddra_line.split("$")
                self.meddra_codes.append(meddra_line[0])
                self.meddra_code_to_meddra_term[meddra_line[0]] = meddra_line[1]
                self.meddra_term_to_meddra_code[meddra_line[1]] = meddra_line[0]
    def meddra_code_to_one_hot_emb(self, meddra_code):
        one_hot_emb = [0]*len(self.meddra_codes)
        one_hot_emb[self.meddra_codes.index(meddra_code)] = 1
        return one_hot_emb
    
CV = ConceptVectorizer('../../Data/External/pt_en.asc')
print('getting thesaurus embeddings...')
CV.thesaurus_embeddings = model.encode(list(CV.meddra_term_to_meddra_code.keys()))

getting thesaurus embeddings...


In [3]:
from transformers import AutoTokenizer

#токенизатор от модели, которую обучаем!
CV.tokenizer = AutoTokenizer.from_pretrained('roberta-base')

In [4]:
import torch

CV.thesaurus_embeddings = torch.tensor(CV.thesaurus_embeddings)
CV.thesaurus_embeddings

tensor([[-0.0016, -0.0660, -0.0317,  ..., -0.0013, -0.0172, -0.0282],
        [-0.0084, -0.0428, -0.0215,  ..., -0.0078,  0.0151,  0.0432],
        [-0.0014, -0.0420, -0.0288,  ..., -0.0399,  0.0124,  0.0470],
        ...,
        [-0.0234, -0.0304, -0.0019,  ...,  0.0780, -0.0503,  0.0214],
        [-0.0026,  0.0083, -0.0171,  ...,  0.0200,  0.0227, -0.0198],
        [-0.0524, -0.0024,  0.0082,  ..., -0.0267, -0.0339,  0.0070]])

<h3>Создадим датасет SMM4H2017</h3>

In [5]:
import jsonlines
import numpy as np
from sklearn.model_selection import train_test_split

In [6]:
ds = []
with open('../../Data/Raw/SMM4H_2017/train.txt') as tr, open('../../Data/Raw/SMM4H_2017/test.txt') as ts:
    train_phrases = []
    train_concepts = []
    test_phrases = []
    test_concepts = []
    for pair in tr.read().split('\n'):
        if pair=='':
            continue
        row_inf = pair.split('\t')
        if row_inf[2] in CV.meddra_codes:
            train_phrases.append(row_inf[1])
            train_concepts.append(row_inf[2])
    for pair in ts.read().split('\n'):
        if pair=='':
            continue
        row_inf = pair.split('\t')
        if row_inf[2] in CV.meddra_codes:
            test_phrases.append(row_inf[1])
            test_concepts.append(row_inf[2])
    
print(test_phrases[0], test_concepts[0]) 

sleepier 10041349


In [7]:
print('Всего фраз в трейне: %s'%len(train_phrases))
print('Всего фраз в тесте: %s'%len(test_phrases))

print('Уникальных фраз в трейне: %s'%len(set(train_phrases)))
print('Уникальных фраз в тесте: %s'%len(set(test_phrases)))

#Посмотрим на статистику разбиения
print('%s концептов не входящих либо в трейн, либо в тест'%len(set.union(set(train_concepts), set(test_concepts)) - set.intersection(set(test_concepts), set(train_concepts))))
print('%s концептов, которые есть в тесте, но нет в трейне'%len(set(test_concepts) - set(train_concepts)))
print('%s концептов, которые есть в трейне, но нет в тесте'%len(set(train_concepts) - set(test_concepts)))

Всего фраз в трейне: 6627
Всего фраз в тесте: 2494
Уникальных фраз в трейне: 2815
Уникальных фраз в тесте: 1189
279 концептов не входящих либо в трейн, либо в тест
31 концептов, которые есть в тесте, но нет в трейне
248 концептов, которые есть в трейне, но нет в тесте


In [8]:
from dataset import MedNormDataset

SMM4H_train = MedNormDataset(train_phrases, train_concepts, CV, use_cuda=True)
SMM4H_test = MedNormDataset(test_phrases, test_concepts, CV, use_cuda=True)

Метки из датасета SMM4H, которых нет в меддре

In [9]:
print(set(train_concepts + test_concepts) - set(CV.meddra_codes))

set()


<h2>Сама модель</h2>

In [12]:
import torch.nn as nn
import torch.nn.functional as F
import torch
#Динамический импорт класса нужной PreTrained модели по автоконфигурации
from transformers import AutoModel

#Все, что нужно указать
model_path = 'roberta-base'

device = 'cuda' if torch.cuda.is_available() else 'cpu'
#device = 'cpu'

class Net(nn.Module):
    def __init__(self, model_path: str, thesaurus_embeddings: torch.tensor):
        super(Net, self).__init__()
        self.transformer = AutoModel.from_pretrained(model_path)
        self.thesaurus_normalized_embs = nn.Parameter(self._normalize_embeddings(thesaurus_embeddings), requires_grad=False)
        
    def forward(self, x):
        emb = self.transformer(**x)
        x = self._mean_pooling(emb, x['attention_mask'])
        #имеем две матрицы x - (batch_size, emb_size) и thesaurus_embeddings - (thesaurus_size, emb_size)
        #надо посчитать косинусную близость близость между каждым вектором x и каждым вложением из тезауруса
        #решение: https://stackoverflow.com/questions/50411191/how-to-compute-the-cosine-similarity-in-pytorch-for-all-rows-in-a-matrix-with-re
        x_n = x.norm(dim=1)[:, None] 
        x_n = x / torch.clamp(x_n, min=1e-8)
        #b_norm = CV.thesaurus_embeddings / torch.clamp(b_, min=1e-9)
        cos_sim = torch.mm(x_n, self.thesaurus_normalized_embs)
        x = F.softmax(cos_sim, dim=1)
        return x
    
    def _normalize_embeddings(self, emb):
        normalized_embs = emb.norm(dim=1)[:, None]
        normalized_embs = emb / torch.clamp(normalized_embs, min=1e-8)
        normalized_embs = normalized_embs.transpose(0, 1)
        return normalized_embs
    
    def _mean_pooling(self, model_output, attention_mask):
        token_embeddings = model_output[0] #First element of model_output contains all token embeddings
        input_mask_expanded = attention_mask.unsqueeze(-1).expand(token_embeddings.size()).float()
        return torch.sum(token_embeddings * input_mask_expanded, 1) / torch.clamp(input_mask_expanded.sum(1), min=1e-8)



#net = Net(model_path, CV.thesaurus_embeddings)
#net.to(device)
#print('Net loaded')

<h2>Обучение модели</h2>

Для большей детерменированности

In [1]:
import os 

os.environ["CUBLAS_WORKSPACE_CONFIG"]=":16:8"
torch.use_deterministic_algorithms(mode=False)
np.random.seed(0)
torch.manual_seed(0)
torch.backends.cudnn.benchmark = False

NameError: name 'torch' is not defined

HyperOpt

In [32]:
from hyperopt import hp
# minimize the objective over the space
from hyperopt import fmin, tpe, space_eval, STATUS_OK
from sklearn.metrics import f1_score

model_path = 'roberta-base'

def train_model_1ep(args):
    lr, batch_size = args['lr'], int(args['batch_size'])
    #if batch_size==0 or batch_size==1:
    #    batch_size=2
    #if batch_size>32:
    #    batch_size=32
    net = Net(model_path, CV.thesaurus_embeddings)
    scaler = torch.cuda.amp.GradScaler()
    net.to(device)
    trainloader = torch.utils.data.DataLoader(SMM4H_train, batch_size=batch_size,
                                          shuffle=False, num_workers=0)
    testloader = torch.utils.data.DataLoader(SMM4H_test, batch_size=1,
                                          shuffle=False)
    criterion = nn.CrossEntropyLoss()
    optimizer = optim.AdamW(net.parameters(), lr=lr)
    #initial_loss = None
    for epoch in range(1, 2):
        net.train()
        #with tqdm(trainloader, unit="batch") as tepoch:
        for data in trainloader:

            tepoch.set_description(f"Epoch {epoch}")

            inputs = data['tokenized_phrases']
            labels = data['one_hot_labels']

            optimizer.zero_grad()
            if device=='cuda':
                with torch.cuda.amp.autocast():
                    outputs = net(inputs)
                    loss = criterion(outputs, labels)
                scaler.scale(loss).backward()
                scaler.step(optimizer)
                scaler.update()
            else:
                outputs = net(inputs)
                loss = criterion(outputs, labels)
                loss.backward()
                optimizer.step()
                #if initial_loss is None:
                #    initial_loss = loss.item()
                #tepoch.set_postfix(loss_decrease = str(initial_loss/loss.item()))
    model_answers = []
    real_answers = []
    net.eval()
    #with tqdm(testloader, unit="batch") as eval_process:
    for data in testloader:

        #tepoch.set_description(f"Progress")

        inputs = data['tokenized_phrases']
        labels = data['one_hot_labels']

        with torch.no_grad():
            pred_meddra_code = CV.meddra_codes[net(inputs).argmax()]


        model_answers.append(pred_meddra_code)
        real_answers.append(data['label_codes'])
    f1 = f1_score(real_answers, model_answers, average='micro')
    print(f1, lr, batch_size)
    return {'loss': -f1,
            'status': STATUS_OK}
    
space = {'lr': hp.uniform('lr', 0.0001, 0.001), 'batch_size': hp.randint('batch_size', 16, 33)}
best = fmin(
    fn=train_model_1ep, # Objective Function to optimize
    space=space, # Hyperparameter's Search Space
    algo=tpe.suggest, # Optimization algorithm (representative TPE)
    max_evals=1000 # Number of optimization attempts
)

print(best)

  0%|          | 0/1000 [00:00<?, ?trial/s, best loss=?]

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaModel: ['lm_head.dense.bias', 'lm_head.decoder.weight', 'lm_head.layer_norm.bias', 'lm_head.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.weight']
- This IS expected if you are initializing RobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


0.7702485966319166                                      
0.00022472662655199916                                  
28                                                      
  0%|          | 1/1000 [00:51<14:20:54, 51.71s/trial, best loss: -0.7702485966319166]

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaModel: ['lm_head.dense.bias', 'lm_head.decoder.weight', 'lm_head.layer_norm.bias', 'lm_head.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.weight']
- This IS expected if you are initializing RobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


0.7626303127506016                                                                    
0.00013335033359553096                                                                
23                                                                                    
  0%|          | 2/1000 [01:56<16:24:18, 59.18s/trial, best loss: -0.7702485966319166]

...

0.768644747393745                                                                       
0.0003286525753249237                                                                   
28                                                                                      
100%|█████████▉| 998/1000 [17:32:40<02:06, 63.26s/trial, best loss: -0.7971130713712912]

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaModel: ['lm_head.dense.bias', 'lm_head.decoder.weight', 'lm_head.layer_norm.bias', 'lm_head.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.weight']
- This IS expected if you are initializing RobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


0.772654370489174                                                                       
0.00017000004893260969                                                                  
19                                                                                      
100%|█████████▉| 999/1000 [17:33:46<01:04, 64.06s/trial, best loss: -0.7971130713712912]

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaModel: ['lm_head.dense.bias', 'lm_head.decoder.weight', 'lm_head.layer_norm.bias', 'lm_head.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.weight']
- This IS expected if you are initializing RobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


0.7590216519647153                                                                      
0.00014851607724981937                                                                  
29                                                                                      
100%|██████████| 1000/1000 [17:34:39<00:00, 63.28s/trial, best loss: -0.7971130713712912]
{'batch_size': 16, 'lr': 0.00019539454649605565}


In [18]:
from tqdm import trange
from tqdm import tqdm
from sklearn.metrics import f1_score

import torch.optim as optim
import torch
import numpy as np

import os

os.environ["CUBLAS_WORKSPACE_CONFIG"]=":16:8"
torch.use_deterministic_algorithms(mode=False)
np.random.seed(0)
torch.manual_seed(0)
torch.backends.cudnn.benchmark = False

In [24]:
args = {'batch_size': 16, 'lr': 0.00019539454649605565}

#os.environ["CUBLAS_WORKSPACE_CONFIG"]=":16:8"
#torch.use_deterministic_algorithms(mode=False)
#np.random.seed(0)
#torch.manual_seed(0)
#torch.backends.cudnn.benchmark = False

lr, batch_size = args['lr'], int(args['batch_size'])
net = Net(model_path, CV.thesaurus_embeddings)
scaler = torch.cuda.amp.GradScaler()
net.to(device)
trainloader = torch.utils.data.DataLoader(SMM4H_train, batch_size=batch_size,
                                      shuffle=False, num_workers=0)
testloader = torch.utils.data.DataLoader(SMM4H_test, batch_size=1,
                                      shuffle=False)
criterion = nn.CrossEntropyLoss()
optimizer = optim.AdamW(net.parameters(), lr=lr)

initial_loss = None
for epoch in range(1, 2):
    net.train()
    with tqdm(trainloader, unit="batch") as tepoch:
        for data in tepoch:

            tepoch.set_description(f"Epoch {epoch}")

            inputs = data['tokenized_phrases']
            labels = data['one_hot_labels']

            optimizer.zero_grad()
            if device=='cuda':
                with torch.cuda.amp.autocast():
                    outputs = net(inputs)
                    loss = criterion(outputs, labels)
                scaler.scale(loss).backward()
                scaler.step(optimizer)
                scaler.update()
            else:
                outputs = net(inputs)
                loss = criterion(outputs, labels)
                loss.backward()
                optimizer.step()
            if initial_loss is None:
                initial_loss = loss.item()
            tepoch.set_postfix(loss_decrease = str(initial_loss/loss.item()))
    model_answers = []
    real_answers = []
    net.eval()
    with tqdm(testloader, unit="batch") as eval_process:
        for data in eval_process:

            #tepoch.set_description(f"Progress")

            inputs = data['tokenized_phrases']
            labels = data['one_hot_labels']

            with torch.no_grad():
                pred_meddra_code = CV.meddra_codes[net(inputs).argmax()]


            model_answers.append(pred_meddra_code)
            real_answers.append(data['label_codes'])

        print('epoch %s'%(epoch))
        print('f1 %s'%f1_score(real_answers, model_answers, average='micro'))
        
            
print('Finished Training')

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaModel: ['lm_head.decoder.weight', 'lm_head.layer_norm.weight', 'lm_head.bias', 'lm_head.layer_norm.bias', 'lm_head.dense.bias', 'lm_head.dense.weight']
- This IS expected if you are initializing RobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
100%|██████████| 2494/2494 [00:27<00:00, 89.55batch/s]

epoch 1
f1 0.7694466720128308
Finished Training


In [ ]:
0.3869286287089014

In [ ]:
0.7626303127506016

In [ ]:
0.7902967121090617

In [ ]:
0.7878909382518043

In [ ]:
0.7878909382518043

15ая эпоха лучшая

In [21]:
initial_loss

10.129648208618164

In [26]:
loss.item()

10.129644393920898

In [29]:
with tqdm(testloader, unit="batch") as eval_process:
    for data in eval_process:

        #tepoch.set_description(f"Progress")

        inputs = data['tokenized_phrases']
        labels = data['one_hot_labels']

        with torch.no_grad():
            pred_meddra_code = CV.meddra_codes[net(inputs).argmax()]


        model_answers.append(pred_meddra_code)
        real_answers.append(data['label_codes'])

    print('epoch %s'%(epoch+4))
    print('f1 %s'%f1_score(real_answers, model_answers, average='micro'))

100%|██████████| 2494/2494 [00:28<00:00, 88.18batch/s] 

epoch 5
f1 0.8340016038492382


<h2>Тест модели с mean_pooling 4 ep</h2>

In [28]:
from sklearn.metrics import classification_report, f1_score
from tqdm import tqdm


net.eval()

model_answers=[]
real_answers=[]

testloader = torch.utils.data.DataLoader(SMM4H_test, batch_size=1,
                                          shuffle=False)


with tqdm(testloader, unit="batch") as eval_process:
    for data in eval_process:

        #tepoch.set_description(f"Progress")

        inputs = data['tokenized_phrases']
        labels = data['one_hot_labels']

        with torch.no_grad():
            pred_meddra_code = CV.meddra_codes[net(inputs).argmax()]


        model_answers.append(pred_meddra_code)
        real_answers.append(data['label_codes'])

f1_score(real_answers, model_answers, average='micro')

100%|██████████| 2494/2494 [00:25<00:00, 96.29batch/s] 


0.8340016038492382

<h2>Тест модели с mean_pooling 3 ep</h2>

In [24]:
from sklearn.metrics import classification_report, f1_score
from tqdm import tqdm


net.eval()

model_answers=[]
real_answers=[]

testloader = torch.utils.data.DataLoader(SMM4H_test, batch_size=1,
                                          shuffle=False)


with tqdm(testloader, unit="batch") as eval_process:
    for data in eval_process:

        #tepoch.set_description(f"Progress")

        inputs = data['tokenized_phrases']
        labels = data['one_hot_labels']

        with torch.no_grad():
            pred_meddra_code = CV.meddra_codes[net(inputs).argmax()]


        model_answers.append(pred_meddra_code)
        real_answers.append(data['label_codes'])

f1_score(real_answers, model_answers, average='micro')

100%|██████████| 2494/2494 [00:26<00:00, 95.16batch/s]


0.8175621491579792

<h2>Тест модели с mean_pooling 2 ep</h2>

In [19]:
from sklearn.metrics import classification_report, f1_score
from tqdm import tqdm


net.eval()

model_answers=[]
real_answers=[]

testloader = torch.utils.data.DataLoader(SMM4H_test, batch_size=1,
                                          shuffle=False)


with tqdm(testloader, unit="batch") as eval_process:
    for data in eval_process:

        #tepoch.set_description(f"Progress")

        inputs = data['tokenized_phrases']
        labels = data['one_hot_labels']

        with torch.no_grad():
            pred_meddra_code = CV.meddra_codes[net(inputs).argmax()]


        model_answers.append(pred_meddra_code)
        real_answers.append(data['label_codes'])

f1_score(real_answers, model_answers, average='micro')

100%|██████████| 2494/2494 [00:26<00:00, 95.26batch/s]


0.8123496391339214

<h2>Тест модели с mean_pooling 1 ep</h2>

In [16]:
from sklearn.metrics import classification_report, f1_score
from tqdm import tqdm


net.eval()

model_answers=[]
real_answers=[]

testloader = torch.utils.data.DataLoader(SMM4H_test, batch_size=1,
                                          shuffle=False)


with tqdm(testloader, unit="batch") as eval_process:
    for data in eval_process:

        #tepoch.set_description(f"Progress")

        inputs = data['tokenized_phrases']
        labels = data['one_hot_labels']

        with torch.no_grad():
            pred_meddra_code = CV.meddra_codes[net(inputs).argmax()]


        model_answers.append(pred_meddra_code)
        real_answers.append(data['label_codes'])

f1_score(real_answers, model_answers, average='micro')

100%|██████████| 2494/2494 [00:27<00:00, 89.66batch/s] 


0.7538091419406576

In [19]:
from sklearn.metrics import classification_report, f1_score
from tqdm import tqdm


net.eval()

model_answers=[]
real_answers=[]

testloader = torch.utils.data.DataLoader(RDR_test, batch_size=1,
                                          shuffle=False)


with tqdm(testloader, unit="batch") as eval_process:
    for data in eval_process:

        #tepoch.set_description(f"Progress")

        inputs = data['tokenized_phrases']
        labels = data['one_hot_labels']

        with torch.no_grad():
            pred_meddra_code = CV.meddra_codes[net(inputs).argmax()]


        model_answers.append(pred_meddra_code)
        real_answers.append(data['label_codes'])

f1_score(real_answers, model_answers, average='micro')

100%|██████████| 1750/1750 [00:21<00:00, 81.52batch/s]


0.72

In [32]:
from sklearn.metrics import classification_report, f1_score
from tqdm import tqdm


net.eval()

model_answers=[]
real_answers=[]

testloader = torch.utils.data.DataLoader(RDR_test, batch_size=1,
                                          shuffle=False)


with tqdm(testloader, unit="batch") as eval_process:
    for data in eval_process:

        #tepoch.set_description(f"Progress")

        inputs = data['tokenized_phrases']
        labels = data['one_hot_labels']

        with torch.no_grad():
            pred_meddra_code = CV.meddra_codes[net(inputs).argmax()]


        model_answers.append(pred_meddra_code)
        real_answers.append(data['label_codes'][0])

f1_score(real_answers, model_answers, average='micro')

100%|██████████| 1750/1750 [00:20<00:00, 87.42batch/s]


0.792

<h2> Тест необученной модели (на всякий случай) </h2>

In [25]:
from sklearn.metrics import classification_report, f1_score
from tqdm import tqdm

#net.train()
net.eval()

model_answers=[]
real_answers=[]

testloader = torch.utils.data.DataLoader(RDR_test, batch_size=1,
                                          shuffle=False)

with tqdm(testloader, unit="batch") as eval_process:
    for data in eval_process:

        #tepoch.set_description(f"Progress")

        inputs = data['tokenized_phrases']
        labels = data['one_hot_labels']

        with torch.no_grad():
            pred_meddra_code = CV.meddra_codes[net(inputs).argmax()]


        model_answers.append(pred_meddra_code)
        real_answers.append(data['label_codes'])

f1_score(real_answers, model_answers, average='micro')

100%|██████████| 1750/1750 [00:05<00:00, 294.15batch/s]


0.17142857142857143

<h2>Инференс</h2>

In [28]:
from random import randint

i = randint(1, len(RDR_test))

net.eval()

phrase = {k: tensor.unsqueeze(0) for k, tensor in RDR_test[i]['tokenized_phrases'].items()}
concept = RDR_test[i]['label_codes']

with torch.no_grad():
    model_answer = CV.meddra_codes[net(phrase).argmax()]
    


print('phrase: %s'%RDR_test[i]['phrases'])
print('model: %s'%CV.meddra_code_to_meddra_term[model_answer])



print('real: %s'%RDR_test[i]['label_terms'])

phrase: температурой 37,8
model: Пирексия
real: Пирексия


Где ошиблась модель

In [51]:
#net = torch.load('./cadec_SoTa_on_RDR_rubert_base_2_epoch.pt')['param_groups']

net.eval()

model_wrong_answers = []
gold_truth_answers = []
phrases = []

testloader = torch.utils.data.DataLoader(RDR_test, batch_size=1,
                                          shuffle=False)

with tqdm(testloader, unit="batch") as eval_process:
    for data in eval_process:

        #tepoch.set_description(f"Progress")

        inputs = data['tokenized_phrases']
        labels = data['one_hot_labels']

        with torch.no_grad():
            pred_meddra_code = CV.meddra_codes[net(inputs).argmax()]
        
        if str(pred_meddra_code)!=str(data['label_codes'][0]):
            model_wrong_answers.append(pred_meddra_code)
            gold_truth_answers.append(data['label_codes'][0])
            phrases.append(data['phrases'][0])
        #model_wrong_answers
        #model_answers.append(pred_meddra_code)
        #real_answers.append(data['label_codes'])
        
import pandas as pd

df = pd.DataFrame(columns=['phrase', 'system output', 'gold markup'])

for phrase, m_a, g_a in zip(phrases, model_wrong_answers, gold_truth_answers):
    new_row = pd.DataFrame({'phrase': [phrase], 'system output': [m_a], 'gold markup': [g_a]})
    df = pd.concat([df, new_row], join='inner', ignore_index=True)
    #gold_truth_answers.append(g_a)
    
df

100%|██████████| 1750/1750 [00:19<00:00, 88.99batch/s]


phrase system output gold markup
0                              раздрожалась      10025482    10022998
1                           чувство тревоги      10033670    10002855
2                      угнетенном состоянии      10025482    10040007
3                        Начала плохо спать      10022437    10062519
4        ухудшилось эмоциональное состояние      10061284    10014551
..                                      ...           ...         ...
359                проблема с кожей на лице      10015150    10000496
360                  шаткая нервная система      10029216    10003549
361  острой респираторной вирусной инфекции      10074831    10062352
362             с гнойно-слизистым секретом      10023848    10039083
363                                    37,3      10037660    10005911

[364 rows x 3 columns]

In [59]:
df.to_csv('rubert_base_RDR_wrong.csv', index=False)

In [74]:
CV.meddra_code_to_meddra_term['CONCEPT_LESS'] = 'CONCEPT_LESS'

In [89]:
import pandas as pd

df = pd.read_csv('elastic_wrong_predictions.csv')
df['system concept'] = df.apply(lambda x: CV.meddra_code_to_meddra_term[str(x['system output'])], axis=1)#], join='outer', ignore_index=True)
df['gold concept'] = df.apply(lambda x: CV.meddra_code_to_meddra_term[str(x['gold markup'])], axis=1)
df

phrase system output  gold markup  \
0                профилактики      10036898     10036898   
1            для профилактики      10036898     10036898   
2                профилактики      10036898     10036898   
3                профилактики      10036898     10036898   
4                     стрессы      10042209     10042209   
...                       ...           ...          ...   
1745              тревожности  CONCEPT_LESS     10033670   
1746  ослабленного иммунитета  CONCEPT_LESS     10021425   
1747                    чихал  CONCEPT_LESS     10041232   
1748                   кашлял  CONCEPT_LESS     10011224   
1749              температура      10005911     10005911   

                   system concept                           gold concept  
0                    Профилактика                           Профилактика  
1                    Профилактика                           Профилактика  
2                    Профилактика                           Профилактика  
3                    Профилактика                           Профилактика  
4                          Стресс                                 Стресс  
...                           ...                                    ...  
1745                 CONCEPT_LESS                     Паническая реакция  
1746                 CONCEPT_LESS  Нарушение со стороны иммунной системы  
1747                 CONCEPT_LESS                                Чихание  
1748                 CONCEPT_LESS                                 Кашель  
1749  Повышенная температура тела            Повышенная температура тела  

[1750 rows x 5 columns]

In [95]:
df_wrong = df[df['system output'].apply(lambda x: int(x) if x!='CONCEPT_LESS' else 'CONCEPT_LESS')!=df['gold markup']]

In [94]:
df_wrong[df_wrong['system output']!='CONCEPT_LESS']

Empty DataFrame
Columns: [phrase, system output, gold markup, system concept, gold concept]
Index: []

In [96]:
df_wrong.to_csv('elastic_RDR_wrong.csv', index=False)

In [80]:
df['system output']

0       True
1       True
2       True
3       True
4       True
        ... 
1745    True
1746    True
1747    True
1748    True
1749    True
Length: 1750, dtype: bool

In [82]:
df['system output']

0           10036898
1           10036898
2           10036898
3           10036898
4           10042209
            ...     
1745    CONCEPT_LESS
1746    CONCEPT_LESS
1747    CONCEPT_LESS
1748    CONCEPT_LESS
1749        10005911
Name: system output, Length: 1750, dtype: object

In [81]:
df['gold markup']

0       10036898
1       10036898
2       10036898
3       10036898
4       10042209
          ...   
1745    10033670
1746    10021425
1747    10041232
1748    10011224
1749    10005911
Name: gold markup, Length: 1750, dtype: int64

In [71]:
df.to_csv('rubert_base_wrong_preds_RDR.csv', index=False)

In [44]:
df.drop('Unnamed: 0', axis=1)

system output  gold markup
0         10025482     10022998
1         10033670     10002855
2         10025482     10040007
3         10022437     10062519
4         10061284     10014551
..             ...          ...
359       10015150     10000496
360       10029216     10003549
361       10074831     10062352
362       10023848     10039083
363       10037660     10005911

[364 rows x 2 columns]

In [33]:
df = pd.DataFrame(columns=['system output', 'gold markup'])

for m_a, g_a in zip(model_wrong_answers, gold_truth_answers):
    new_row = pd.DataFrame({'system output': [m_a], 'gold markup': [g_a]})
    df = pd.concat([df, new_row], join='inner', ignore_index=True)
    #gold_truth_answers.append(g_a)
    
df

system output gold markup
0         10036898    10036898
1         10036898    10036898
2         10036898    10036898
3         10036898    10036898
4         10042209    10042209
...            ...         ...
1745      10033670    10033670
1746      10021425    10021425
1747      10041232    10041232
1748      10011224    10011224
1749      10005911    10005911

[1750 rows x 2 columns]

In [19]:
net.keys()

dict_keys(['state', 'param_groups'])

<h2>Сохранение и загрузка модели</h2>

In [15]:
torch.save(net, './cadec_SoTa_50_ep.pt')
torch.save(optimizer.state_dict(), './cadec_SoTa_50_ep_opt.pt')

In [30]:
the_model = torch.load('./cadec_SoTa_on_RDR_rubert_right_exp.pt')

Покажем, что это ТА ЖЕ модель

In [32]:
the_model.eval()

model_answers=[]
real_answers=[]

testloader = torch.utils.data.DataLoader(RDR_test, batch_size=1,
                                          shuffle=False)


with tqdm(testloader, unit="batch") as eval_process:
    for data in eval_process:


        inputs = data['tokenized_phrases']
        labels = data['one_hot_labels']

        with torch.no_grad():
            pred_meddra_code = CV.meddra_codes[the_model(inputs).argmax()]


        model_answers.append(pred_meddra_code)
        real_answers.append(data['label_codes'])

f1_score(real_answers, model_answers, average='micro')

100%|██████████| 1750/1750 [00:06<00:00, 259.93batch/s]


0.5891428571428572

In [1]:
import torch

opt = torch.load('./cadec_SoTa_50_ep_opt.pt')
opt

{'state': {1: {'step': 20335,
   'exp_avg': tensor([[-2.4216e-08,  1.5063e-08, -5.9635e-10,  ...,  1.8953e-08,
             3.2177e-08,  5.4440e-08],
           [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
             0.0000e+00,  0.0000e+00],
           [ 6.9163e-09,  2.5762e-08, -2.2621e-08,  ...,  2.3584e-09,
             1.8493e-08,  4.9894e-08],
           ...,
           [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
             0.0000e+00,  0.0000e+00],
           [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
             0.0000e+00,  0.0000e+00],
           [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
             0.0000e+00,  0.0000e+00]], device='cuda:0'),
   'exp_avg_sq': tensor([[1.9701e-15, 2.2903e-15, 3.0738e-15,  ..., 3.6316e-15, 2.0951e-15,
            4.0135e-15],
           [0.0000e+00, 0.0000e+00, 0.0000e+00,  ..., 0.0000e+00, 0.0000e+00,
            0.0000e+00],
           [1.4487e-15, 2.5023e-15, 4.1912e-15,  .